In [2]:
from notepad import WaterStorage, Heatpump
# from pyrecoy.forecasts import Mipf
%load_ext autoreload
%autoreload 2

In [4]:
import pandas as pd
# import cufflinks
# cufflinks.go_offline()
from numpy.polynomial import Polynomial
import numpy as np

In [5]:
rng = pd.date_range('2018-11-01 00:00:00', end='2018-11-01 12:00:00', freq='15T' )

price_data = pd.DataFrame(np.random.randint(30, 110, size=(len(rng))), 
                  columns=['ForeNeg'], 
                  index=rng)

price_data['ForePos'] = np.random.randint(20, 50, size=(len(rng)))

price_data.head()

ForeNeg  ForePos
2018-11-01 00:00:00       91       34
2018-11-01 00:15:00       39       31
2018-11-01 00:30:00       52       29
2018-11-01 00:45:00      108       42
2018-11-01 01:00:00       49       36

In [6]:
# mipf = Mipf(
#     start='2018-11-01', 
#     end='2018-11-02', 
#     tidy=True, 
#     include_nextQ=False,
#     folder_path=r"C:\Users\Shahla Huseynova\Recoy\Recoy - Documents\03 - Libraries\12 - Data Management\Forecast Data"
# ).data
# # mipf.columns
# price_data = mipf[['DAM', 'POS', 'NEG', 'ForeNeg', 'ForePos']]
# price_data = price_data.resample('15T').mean()
# price_data

In [7]:
data = pd.read_excel('Demand_Data_Smurfit_Preprocessed.xlsx', sheet_name='nov2018', index_col=0)
start, end = '2018-11-01 00:00:00', '2018-11-01 12:00:00'
df = data[start:end]
df = df.resample('15T', origin=start).mean()
df=df.drop(['Unnamed: 7', 'Unnamed: 8', 'Unnamed: 9', 'Unnamed: 10', 'Unnamed: 11', 'Unnamed: 12'], axis=1)

df.head()

Tsource (VDG)  Tsink (VDG)  MW (VDG)  Tsource (NDG)  \
2018-11-01 00:00:00      64.964783   142.003109       0.0      19.897433   
2018-11-01 00:15:00      54.578777   138.960493       0.0      17.950905   
2018-11-01 00:30:00      65.166672   139.885329       0.0      33.500757   
2018-11-01 00:45:00      65.358078   139.731901       0.0      42.203876   
2018-11-01 01:00:00      64.947536   139.577871       0.0      18.702675   

                     Tsink (NDG)  MW (NDG)  
2018-11-01 00:00:00   147.731814       0.0  
2018-11-01 00:15:00   148.138964       0.0  
2018-11-01 00:30:00   147.585426       0.0  
2018-11-01 00:45:00   147.547612       0.0  
2018-11-01 01:00:00   148.260335       0.0

In [8]:
# df[['Tsource (VDG)', 'Tsink (VDG)']].iplot()

In [9]:
waterstorage = WaterStorage(
    name='MyStorage',
    max_power=10,
    min_power=-10,
    roundtrip_eff=0.90,
    capacity_per_volume = 50 * 1e-3,
    volume = 1000,
    lifetime = 25,
    temperature = 368, #K
    min_storagelevel = 5,
    # max_storagelevel = 50
    
)
waterstorage.set_freq('15T')
waterstorage.set_storagelevel(15)
waterstorage.storagelevel

15

In [110]:
Tsink = 140  #Celcius
Tsource = 60
Tref = 0
hp_capacity = 31 #MW
process_demand_MW = 25 #MW
Cp = 4190  #J/kgK
MWtoJs = 1000_000
# hp_capacity *= MW_to_J_per_s
# process_demand_MW *= MW_to_J_per_s
efficiency = 0.9
Tstorage = 95

print('process demand', process_demand_MW)
# hp_capacity vs hp_load?

process demand 25


In [111]:
waterstorage.max_storage_capacity

50.0

In [112]:
def hp_mass_flow (hp_capacity, Tsink, Tref, Cp):
    return hp_capacity /(Cp*(Tsink - Tref)) 

def process_mass_flow (process_demand_MW, Tsink, Tref, Cp):
    return process_demand_MW /(Cp*(Tsink - Tref)) 

def cop_curve(Tsink, Tsource):
    c0 = Tsink / (Tsink - Tsource)  
    return Polynomial([c0])

charge_mass_flow = hp_mass_flow (hp_capacity, Tsink, Tref, Cp) - process_mass_flow (process_demand_MW, Tsink, Tref, Cp)


def energy_to_storage(hp_capacity, process_demand_MW):
    return hp_capacity - process_demand_MW


discharged_heat = energy_to_storage(hp_capacity, process_demand_MW) #MW

# def charged_heat (charge_mass_flow, Cp, Tsink, Tref):
#     return (charge_mass_flow * Cp * (Tsink - Tref)) / MW_to_J_per_s

# discharged_heat = charged_heat(charge_mass_flow, Cp, Tsink, Tref)  #MW

def discharge_mass_flow (discharged_heat, Cp, Tstorage, Tref):
    return discharged_heat*MWtoJs/(Cp*(Tstorage - Tref))

def Tsource_calculation(Tstorage, discharge_mass_flow, Tsource, process_mass_flow):
    return ((Tstorage * discharge_mass_flow + Tsource * process_mass_flow)
 / (discharge_mass_flow + process_mass_flow))


# charged_heat can be also defined as hp_capacity-process_demand_MW

In [113]:
discharged_heat = energy_to_storage(hp_capacity,19.585104)

print(discharged_heat)

discharge_mass = discharge_mass_flow(discharged_heat, Cp, 140+273, Tref+273)

print(discharge_mass)

11.414895999999999
19.459420388680527


In [114]:
# heatpump = Heatpump("heatpump1", 50, cop_curve, 10)
# heatpump.set_heat_output(50, Tsource=333, Tsink=413)
cop_curve(140, 60)

heatpump = Heatpump(
    name='Heatpump',
    max_th_power=40,
    min_th_power=5,
    cop_curve=cop_curve
)

heatpump.__dict__



{'name': 'Heatpump',
 'max_th_power': 40,
 'min_th_power': 5,
 'cop_curve': <function __main__.cop_curve(Tsink, Tsource)>}

In [115]:
heatpump.get_cop(50, Tsource=333, Tsink=413)


5.1625

In [116]:
# def test_heatpump_and_waterstorage_system(Tsink, Tsource, process_demand_MW, e_price):
#     """
#     1. Follow a certain logic based on given price:
#         - If price is low --> Heatpump at full power, and charge the heatbuffer
#         - If price is high --> Discharge the heat buffer, and increase Tsource, which will increase COP
#     2. Above logic should adhere to a couple of constraints:
#         - Storage levels
#         - Capacity of the heat pump 
#         - Process demand
#         - ....
#     3. This function should contain: 
#         - Heat pump 
#         - Water storage
#         - Interactions / logic between them
#     4. Output of the function:
#         - Power of the heatpump (MWe)
#         - "New" water storage level
#         - (optional) Thermal output of the heatpump
#         - (optional) In/outflow from the storage
#     """
    
#     if e_price < 50:
#         hp_load = heatpump.max_th_power
#         energy_to_storage = hp_load - process_demand_MW
#         waterstorage.charge(energy_to_storage)
#         new_cl = waterstorage.storagelevel
#     if e_price > 100:
#         energy_from_storage = discharged_heat
#         waterstorage.discharge(energy_from_storage)
#         new_cl = waterstorage.storagelevel
        
#         def Tsource_calculation(Tstorage, discharge_mass_flow, Tsource, process_mass_flow):
#             return ((Tstorage * discharge_mass_flow(discharged_heat, Cp, Tstorage, Tref) + Tsource * process_mass_flow(process_demand_MW, Tsink, Tref, Cp))
#                     / (discharge_mass_flow(discharged_heat, Cp, Tstorage, Tref) + process_mass_flow(process_demand_MW, Tsink, Tref, Cp)))
#         new_COP = cop_curve (Tsink, Tsource_calculation(Tstorage, discharge_mass_flow, Tsource, process_mass_flow))
#         hp_load = heatpump.set_heat_output(process_demand_MW, Tsink, Tsource) #bu da hemcinin set load assetin funksiyasidir, 
#         #heatpump da overwrite edilib. men evezinde yazdim ki set_heat_output
#         #sen gor hansi funksiya sene lazimdir.

#     return hp_load, new_cl

In [117]:
# waterstorage.get_soc (30, 50)

In [118]:
for col in price_data.columns:
    df[col] = price_data[col]
df.head(10)
# iki dataframeni birlesdirdik burda

Tsource (VDG)  Tsink (VDG)   MW (VDG)  Tsource (NDG)  \
2018-11-01 00:00:00      64.964783   142.003109   0.000000      19.897433   
2018-11-01 00:15:00      54.578777   138.960493   0.000000      17.950905   
2018-11-01 00:30:00      65.166672   139.885329   0.000000      33.500757   
2018-11-01 00:45:00      65.358078   139.731901   0.000000      42.203876   
2018-11-01 01:00:00      64.947536   139.577871   0.000000      18.702675   
2018-11-01 01:15:00      65.073433   139.423357   0.000000      19.903652   
2018-11-01 01:30:00      47.711559   140.328730   0.000000      19.574467   
2018-11-01 01:45:00      29.525829   140.298902   0.000000      17.065464   
2018-11-01 02:00:00      65.715569   139.991650  10.139587      49.339708   
2018-11-01 02:15:00      65.929909   148.342325  19.585104      61.721718   

                     Tsink (NDG)  MW (NDG)  ForeNeg  ForePos   hp_mass  \
2018-11-01 00:00:00   147.731814  0.000000       91       34  0.000052   
2018-11-01 00:15:00   148.138964  0.000000       39       31  0.000053   
2018-11-01 00:30:00   147.585426  0.000000       52       29  0.000053   
2018-11-01 00:45:00   147.547612  0.000000      108       42  0.000053   
2018-11-01 01:00:00   148.260335  0.000000       49       36  0.000053   
2018-11-01 01:15:00   149.186865  0.000000       75       27  0.000053   
2018-11-01 01:30:00   147.800016  0.000000      100       22  0.000053   
2018-11-01 01:45:00   147.906886  0.000000       54       45  0.000053   
2018-11-01 02:00:00   149.603741  3.333301      100       42  0.000053   
2018-11-01 02:15:00   155.887905  6.455359       85       36  0.000050   

                     process_mass                   COP  charge_mass  
2018-11-01 00:00:00      0.000000   (5.386969459992516)     0.000052  
2018-11-01 00:15:00      0.000000   (4.882106135030027)     0.000053  
2018-11-01 00:30:00      0.000000  (5.5258665771869335)     0.000053  
2018-11-01 00:45:00      0.000000   (5.549424302045392)     0.000053  
2018-11-01 01:00:00      0.000000   (5.528286493353138)     0.000053  
2018-11-01 01:15:00      0.000000   (5.547058190973266)     0.000053  
2018-11-01 01:30:00      0.000000   (4.462765657815752)     0.000053  
2018-11-01 01:45:00      0.000000   (3.731041234226957)     0.000053  
2018-11-01 02:00:00      0.000017   (5.560223997670469)     0.000036  
2018-11-01 02:15:00      0.000032   (5.112607341877656)     0.000018

In [119]:
# for i in df.index:
#     df.loc[i, 'hp_mass'] = hp_mass_flow(hp_capacity, df.loc[i, 'Tsink (VDG)'], Tref, Cp)
#     df.loc[i, 'process_mass'] = process_mass_flow(df.loc[i, 'MW (VDG)'], df.loc[i, 'Tsink (VDG)'],Tref, Cp)
#     df.loc[i, 'COP'] = cop_curve(df.loc[i, 'Tsink (VDG)']+273, df.loc[i, 'Tsource (VDG)']+273)
#     df.loc[i, 'charge_mass'] = df.loc[i, 'hp_mass'] - df.loc[i, 'process_mass']
# #     df.loc[i, 'charged_heat'] = charged_heat(df.loc[i, 'charge_mass'], Cp, df.loc[i, 'Tsink (VDG)']+273, Tref + 273)
# #     df.loc[i, 'discharged_heat'] = charged_heat(df.loc[i, 'charge_mass'], Cp, df.loc[i, 'Tsink (VDG)']+273, Tref + 273)
# #     df.loc[i, 'discharge_mass'] = discharge_mass_flow(df.loc[i, 'discharged_heat'], Cp, Tstorage+273, Tref+273)
# #     df.loc[i, 'Tsource_new'] = Tsource_calculation(Tstorage + 273, df.loc[i, 'discharge_mass'], df.loc[i, 'Tsource (VDG)']+273, df.loc[i, 'process_mass'])
# #     df.loc[i, 'new_COP'] = cop_curve(df.loc[i, 'Tsink (VDG)']+273, df.loc[i, 'Tsource_new'])
    
# df.head(10)
# Tsource_new should be in the nested function but now it is calculated separately, need to be checked again
# discharge_mass were checked manually,there is  very slight change in the last decimals that's why seems constant here, but it calculates correctly.

# process mass results are wrong

In [125]:
# df.index = df.index.tz_localize('Europe/Amsterdam')
for i in df.index:
    # if df.loc[i, 'ForePos'] < 50:
    #     hp_load = heatpump.max_th_power
    #     energy_to_storage = hp_load - df.loc[i, 'MW (VDG)']
    #     waterstorage.charge(energy_to_storage)
    #     new_cl = waterstorage.storagelevel
    #     print(new_cl)
    if price_data.loc[i,'ForeNeg'] > 100:
        # discharged_heat = energy_to_storage(hp_capacity, df.loc[i, 'MW (VDG)'])
        energy_from_storage = energy_to_storage(hp_capacity, df.loc[i, 'MW (VDG)'])
        waterstorage.discharge(energy_from_storage)
        new_cl = waterstorage.storagelevel
        discharge_mass = discharge_mass_flow(energy_from_storage, Cp, df.loc[i, 'Tsink (VDG)']+273, Tref + 273)
        print(discharge_mass)
        Tsource_new = Tsource_calculation(Tstorage, discharge_mass, Tsource, process_mass_flow(df.loc[i, 'MW (VDG)'], df.loc[i, 'Tsink (VDG)'], Tref, Cp))
        new_COP = cop_curve (df.loc[i, 'Tsink (VDG)']+273, Tsource_new+273)
        # # print(new_COP) 

52.94831003899137
17.232571785757365
15.690906523897725
15.833641124244465
15.766858500063137


In [18]:
for i in df.index:
    df.loc[i, 'charged_heat'] = energy_to_storage(hp_capacity, df.loc[i, 'MW (VDG)'])
    df.loc[i, 'discharged_heat'] =  df.loc[i, 'charged_heat']
    df.loc[i, 'discharge_mass'] = discharge_mass_flow(df.loc[i, 'discharged_heat'], Cp, Tstorage+273, Tref+273)
    df.loc[i, 'Tsource_new'] = Tsource_calculation(Tstorage + 273, df.loc[i, 'discharge_mass'], df.loc[i, 'Tsource (VDG)']+273, df.loc[i, 'process_mass'])
    df.loc[i, 'new_COP'] = cop_curve(df.loc[i, 'Tsink (VDG)']+273, df.loc[i, 'Tsource_new'])
    
df.head(10)

TypeError: 'numpy.float64' object is not callable

In [43]:
# for i in df.index:
#     # df.loc[i, 'MWe'] = test_heatpump_and_waterstorage_system(df.loc[i, 'Tsink (VDG)']+273, df.loc[i, 'Tsource (VDG)']+273, df.loc[i, 'MW (VDG)'], 130)[0][0]
#     df.loc[i, 'new_cl'] = test_heatpump_and_waterstorage_system(df.loc[i, 'Tsink (VDG)']+273, df.loc[i, 'Tsource (VDG)']+273, df.loc[i, 'MW (VDG)'], 30)[1]


In [19]:
df[:10]

Tsource (VDG)  Tsink (VDG)   MW (VDG)  Tsource (NDG)  \
2018-11-01 00:00:00      64.964783   142.003109   0.000000      19.897433   
2018-11-01 00:15:00      54.578777   138.960493   0.000000      17.950905   
2018-11-01 00:30:00      65.166672   139.885329   0.000000      33.500757   
2018-11-01 00:45:00      65.358078   139.731901   0.000000      42.203876   
2018-11-01 01:00:00      64.947536   139.577871   0.000000      18.702675   
2018-11-01 01:15:00      65.073433   139.423357   0.000000      19.903652   
2018-11-01 01:30:00      47.711559   140.328730   0.000000      19.574467   
2018-11-01 01:45:00      29.525829   140.298902   0.000000      17.065464   
2018-11-01 02:00:00      65.715569   139.991650  10.139587      49.339708   
2018-11-01 02:15:00      65.929909   148.342325  19.585104      61.721718   

                     Tsink (NDG)  MW (NDG)  ForeNeg  ForePos    hp_mass  \
2018-11-01 00:00:00   147.731814  0.000000      109       43  52.101451   
2018-11-01 00:15:00   148.138964  0.000000       34       46  53.242241   
2018-11-01 00:30:00   147.585426  0.000000       45       48  52.890236   
2018-11-01 00:45:00   147.547612  0.000000       94       38  52.948310   
2018-11-01 01:00:00   148.260335  0.000000      102       24  53.006741   
2018-11-01 01:15:00   149.186865  0.000000       69       40  53.065485   
2018-11-01 01:30:00   147.800016  0.000000       78       46  52.723117   
2018-11-01 01:45:00   147.906886  0.000000       94       23  52.734326   
2018-11-01 02:00:00   149.603741  3.333301       97       24  52.850067   
2018-11-01 02:15:00   155.887905  6.455359      105       44  49.874963   

                     process_mass                   COP  charge_mass  
2018-11-01 00:00:00      0.000000   (5.386969459992516)    52.101451  
2018-11-01 00:15:00      0.000000   (4.882106135030027)    53.242241  
2018-11-01 00:30:00      0.000000  (5.5258665771869335)    52.890236  
2018-11-01 00:45:00      0.000000   (5.549424302045392)    52.948310  
2018-11-01 01:00:00      0.000000   (5.528286493353138)    53.006741  
2018-11-01 01:15:00      0.000000   (5.547058190973266)    53.065485  
2018-11-01 01:30:00      0.000000   (4.462765657815752)    52.723117  
2018-11-01 01:45:00      0.000000   (3.731041234226957)    52.734326  
2018-11-01 02:00:00      0.000017   (5.560223997670469)    52.850049  
2018-11-01 02:15:00      0.000032   (5.112607341877656)    49.874932

In [22]:
# data['Total demand'] = data['MW (VDG)'] + data['MW (NDG)']
# data = data[start:end]
# fig_demands_nov2018 = data['Total demand'].resample('1H').mean().iplot(
#     title='Smurfit Kappa: Heat demand in MW', 
#     yTitle='MW', 
#     asFigure=True,
#     dimensions=(800, 400)
# )
# fig_demands_nov2018

In [23]:
# import plotly.express as px

# fig = px.line(df['new_cl'])
# fig.show()

In [24]:
df.index = df.index.tz_localize('Europe/Amsterdam')

In [26]:
for col in price_data.columns:
    df[col] = price_data[col]

df['nomination_MWh'] = df['DAM'] * df['MW (VDG)']
df['heatpump_cons_MWh'] = 9
df['imbalance_MWh'] = df['nomination_MWh'] - df['heatpump_cons_MWh']
df['day-ahead costs'] = df['nomination_MWh'] * df['DAM'] 

is_pos = df['imbalance_MWh'] > 0
df.loc[is_pos, 'imbalance costs'] = -df.loc[is_pos, 'imbalance_MWh'] * df['POS'] 

is_neg = df['imbalance_MWh'] < 0
df.loc[is_neg, 'imbalance costs'] = -df.loc[is_neg, 'imbalance_MWh'] * df['NEG'] 

df['total cost'] = df['day-ahead costs'] + df['imbalance costs']

In [37]:
df[:10]

Tsource (VDG)  Tsink (VDG)   MW (VDG)  Tsource (NDG)  \
2018-11-01 00:00:00      64.964783   142.003109   0.000000      19.897433   
2018-11-01 00:15:00      54.578777   138.960493   0.000000      17.950905   
2018-11-01 00:30:00      65.166672   139.885329   0.000000      33.500757   
2018-11-01 00:45:00      65.358078   139.731901   0.000000      42.203876   
2018-11-01 01:00:00      64.947536   139.577871   0.000000      18.702675   
2018-11-01 01:15:00      65.073433   139.423357   0.000000      19.903652   
2018-11-01 01:30:00      47.711559   140.328730   0.000000      19.574467   
2018-11-01 01:45:00      29.525829   140.298902   0.000000      17.065464   
2018-11-01 02:00:00      65.715569   139.991650  10.139587      49.339708   
2018-11-01 02:15:00      65.929909   148.342325  19.585104      61.721718   

                     Tsink (NDG)  MW (NDG)    hp_mass  process_mass  \
2018-11-01 00:00:00   147.731814  0.000000  52.101451      0.000042   
2018-11-01 00:15:00   148.138964  0.000000  53.242241      0.000043   
2018-11-01 00:30:00   147.585426  0.000000  52.890236      0.000043   
2018-11-01 00:45:00   147.547612  0.000000  52.948310      0.000043   
2018-11-01 01:00:00   148.260335  0.000000  53.006741      0.000043   
2018-11-01 01:15:00   149.186865  0.000000  53.065485      0.000043   
2018-11-01 01:30:00   147.800016  0.000000  52.723117      0.000043   
2018-11-01 01:45:00   147.906886  0.000000  52.734326      0.000043   
2018-11-01 02:00:00   149.603741  3.333301  52.850067      0.000043   
2018-11-01 02:15:00   155.887905  6.455359  49.874963      0.000040   

                                      COP  charge_mass  ...  ForeNeg  ForePos  \
2018-11-01 00:00:00   (5.386969459992516)    52.101409  ...      NaN      NaN   
2018-11-01 00:15:00   (4.882106135030027)    53.242198  ...      NaN      NaN   
2018-11-01 00:30:00  (5.5258665771869335)    52.890193  ...      NaN      NaN   
2018-11-01 00:45:00   (5.549424302045392)    52.948267  ...      NaN      NaN   
2018-11-01 01:00:00   (5.528286493353138)    53.006698  ...      NaN      NaN   
2018-11-01 01:15:00   (5.547058190973266)    53.065442  ...      NaN      NaN   
2018-11-01 01:30:00   (4.462765657815752)    52.723074  ...      NaN      NaN   
2018-11-01 01:45:00   (3.731041234226957)    52.734283  ...      NaN      NaN   
2018-11-01 02:00:00   (5.560223997670469)    52.850024  ...      NaN      NaN   
2018-11-01 02:15:00   (5.112607341877656)    49.874923  ...      NaN      NaN   

                     charged_heat  discharged_heat  nomination_MWh  \
2018-11-01 00:00:00     30.999975        30.999975             NaN   
2018-11-01 00:15:00           NaN              NaN             NaN   
2018-11-01 00:30:00           NaN              NaN             NaN   
2018-11-01 00:45:00           NaN              NaN             NaN   
2018-11-01 01:00:00           NaN              NaN             NaN   
2018-11-01 01:15:00           NaN              NaN             NaN   
2018-11-01 01:30:00           NaN              NaN             NaN   
2018-11-01 01:45:00           NaN              NaN             NaN   
2018-11-01 02:00:00           NaN              NaN             NaN   
2018-11-01 02:15:00           NaN              NaN             NaN   

                     heatpump_cons_MWh  imbalance_MWh  day-ahead costs  \
2018-11-01 00:00:00                  9            NaN              NaN   
2018-11-01 00:15:00                  9            NaN              NaN   
2018-11-01 00:30:00                  9            NaN              NaN   
2018-11-01 00:45:00                  9            NaN              NaN   
2018-11-01 01:00:00                  9            NaN              NaN   
2018-11-01 01:15:00                  9            NaN              NaN   
2018-11-01 01:30:00                  9            NaN              NaN   
2018-11-01 01:45:00                  9            NaN              NaN   
2018-11-01 02:00:00                  9            NaN         